# Neural Prophet
### Kaggle 
score = 0.410

In [1]:
import pandas as pd
from neuralprophet import NeuralProphet

# 1️⃣ Cargar los datasets
sellin = pd.read_csv("datasets/sell-in.csv", sep='\t')
productos = pd.read_csv("datasets/tb_productos.csv", sep='\t')
stocks = pd.read_csv("datasets/tb_stocks.csv", sep='\t')
productos_a_predecir = pd.read_csv("datasets/product_id_apredecir201912.csv")

# Crear DataFrame principal
df = sellin.merge(productos, on="product_id", how="left").merge(stocks, on=["product_id", "periodo"], how="left")
df['periodo_dt'] = pd.to_datetime(df['periodo'].astype(str), format='%Y%m')

# Sumarizar ventas por periodo y producto
ventas = df.groupby(['periodo', 'product_id']).agg({'tn':'sum'}).reset_index()
ventas['periodo_dt'] = pd.to_datetime(ventas['periodo'].astype(str), format='%Y%m')

# Determinar min y max periodo por producto
vida_producto = ventas.groupby('product_id')['periodo_dt'].agg(['min','max']).reset_index()

# Crear DataFrame expandido con todos <periodo, producto>
all_periods = []
for _, row in vida_producto.iterrows():
    pid = row['product_id']
    periods = pd.date_range(row['min'], row['max'], freq='MS')
    for p in periods:
        all_periods.append((pid, p))
df_full = pd.DataFrame(all_periods, columns=['product_id','periodo_dt'])

# Unir con ventas reales
ventas = ventas[['product_id','periodo_dt','tn']]
df_pp = df_full.merge(ventas, on=['product_id','periodo_dt'], how='left')
df_pp['tn'] = df_pp['tn'].fillna(0)
df_pp['ds'] = df_pp['periodo_dt']
df_pp['y'] = df_pp['tn']

# Filtrar solo productos a predecir
productos_ids = productos_a_predecir['product_id'].unique()

# 2️⃣ Entrenar un modelo por producto a predecir
resultados = []
fecha_prediccion = pd.to_datetime('2020-02-01')

for pid in productos_ids:
    df_prod = df_pp[df_pp['product_id']==pid][['ds','y']].sort_values('ds')
    
    if len(df_prod) < 3:
        print(f"⏩ Saltando producto {pid}: muy pocos datos.")
        resultados.append({'product_id': pid, 'periodo': 202002, 'tn_pred': None})
        continue
    
    m = NeuralProphet(n_lags=12, n_forecasts=2, epochs=100, yearly_seasonality=True)
    try:
        m.fit(df_prod, freq='MS', progress='bar')
        future = m.make_future_dataframe(df_prod, periods=2, n_historic_predictions=False)
        forecast = m.predict(future)
        # Extraer yhat2 (predicción para febrero 2020)
        y_pred = forecast.loc[forecast['ds']==fecha_prediccion, 'yhat2'].values[0]
        resultados.append({'product_id': pid, 'periodo': 202002, 'tn_pred': y_pred})
    except Exception as e:
        print(f"❌ Error en producto {pid}: {e}")
        resultados.append({'product_id': pid, 'periodo': 202002, 'tn_pred': None})

# 3️⃣ Guardar resultados
df_result = pd.DataFrame(resultados)
df_result.to_csv('./kaggle/neuralprophet_feb2020.csv', index=False)
print("✅ Predicciones para febrero 2020 guardadas en ./kaggle/neuralprophet_feb2020.csv")

WARNING - (NP.forecaster.fit) - When Global modeling with local normalization, metrics are displayed in normalized scale.
WARNING - (py.warnings._showwarnmsg) - c:\Users\Usuario\AppData\Local\Programs\Python\Python311\Lib\site-packages\neuralprophet\df_utils.py:1152: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = pd.to_datetime(ds_col, utc=True).view(dtype=np.int64)

INFO - (NP.df_utils._infer_frequency) - Major frequency MS corresponds to [97.222]% of the data.
WARNING - (py.warnings._showwarnmsg) - c:\Users\Usuario\AppData\Local\Programs\Python\Python311\Lib\site-packages\neuralprophet\df_utils.py:1152: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = pd.to_datetime(ds_col, utc=True).view(dtype=np.int64)

WARNING - (py.warnings._showwarnmsg) - c:\Users\Usuario\AppData\Local\Pro

Training: |          | 0/? [00:00<?, ?it/s]

WARNING - (NP.config.set_lr_finder_args) - Learning rate finder: The number of batches (3) is too small than the required number                     for the learning rate finder (203). The results might not be optimal.


Finding best initial lr:   0%|          | 0/203 [00:00<?, ?it/s]

WARNING - (py.warnings._showwarnmsg) - c:\Users\Usuario\AppData\Local\Programs\Python\Python311\Lib\site-packages\pytorch_lightning\utilities\data.py:79: Trying to infer the `batch_size` from an ambiguous collection. The batch size we found is 8. To avoid any miscalculations, use `self.log(..., batch_size=batch_size)`.

WARNING - (py.warnings._showwarnmsg) - c:\Users\Usuario\AppData\Local\Programs\Python\Python311\Lib\site-packages\pytorch_lightning\utilities\data.py:79: Trying to infer the `batch_size` from an ambiguous collection. The batch size we found is 7. To avoid any miscalculations, use `self.log(..., batch_size=batch_size)`.



...

Training: |          | 0/? [00:00<?, ?it/s]

WARNING - (py.warnings._showwarnmsg) - c:\Users\Usuario\AppData\Local\Programs\Python\Python311\Lib\site-packages\neuralprophet\df_utils.py:1152: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = pd.to_datetime(ds_col, utc=True).view(dtype=np.int64)

INFO - (NP.df_utils._infer_frequency) - Major frequency MS corresponds to [93.333]% of the data.
WARNING - (py.warnings._showwarnmsg) - c:\Users\Usuario\AppData\Local\Programs\Python\Python311\Lib\site-packages\neuralprophet\df_utils.py:1152: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = pd.to_datetime(ds_col, utc=True).view(dtype=np.int64)

WARNING - (py.warnings._showwarnmsg) - c:\Users\Usuario\AppData\Local\Programs\Python\Python311\Lib\site-packages\neuralprophet\df_utils.py:1152: FutureWarning: Series.view is deprecated and will

Predicting: |          | 0/? [00:00<?, ?it/s]

INFO - (NP.df_utils.return_df_in_original_format) - Returning df with no ID column
WARNING - (NP.forecaster.fit) - When Global modeling with local normalization, metrics are displayed in normalized scale.
WARNING - (NP.forecaster.fit) - When Global modeling with local normalization, metrics are displayed in normalized scale.
WARNING - (NP.forecaster.fit) - When Global modeling with local normalization, metrics are displayed in normalized scale.
WARNING - (NP.forecaster.fit) - When Global modeling with local normalization, metrics are displayed in normalized scale.


❌ Error en producto 21265: Dataframe has less than n_forecasts + n_lags rows. Forecasting not possible. Please either use a larger dataset, or adjust the model parameters.
❌ Error en producto 21266: Dataframe has less than n_forecasts + n_lags rows. Forecasting not possible. Please either use a larger dataset, or adjust the model parameters.
❌ Error en producto 21267: Dataframe has less than n_forecasts + n_lags rows. Forecasting not possible. Please either use a larger dataset, or adjust the model parameters.
❌ Error en producto 21276: Dataframe has less than n_forecasts + n_lags rows. Forecasting not possible. Please either use a larger dataset, or adjust the model parameters.
✅ Predicciones para febrero 2020 guardadas en ./kaggle/neuralprophet_feb2020.csv


In [ ]:
df_result['tn_pred'] = df_result['tn_pred'].fillna(0)
df_result['tn_pred'] = df_result['tn_pred'].apply(lambda x: 0 if x < 0 else x)

In [4]:
df_result

product_id  periodo      tn_pred
0         20001   202002  1282.631958
1         20002   202002  1019.728638
2         20003   202002   850.583252
3         20004   202002   428.728302
4         20005   202002   639.941406
..          ...      ...          ...
775       21263   202002     0.000000
776       21265   202002     0.000000
777       21266   202002     0.000000
778       21267   202002     0.000000
779       21276   202002     0.000000

[780 rows x 3 columns]

In [5]:
df_result.rename(columns={'tn_pred': 'tn'}, inplace=True)
df_result.drop(columns=['periodo'], inplace=True)

In [8]:
df_result.to_csv('./kaggle/neuralprophet_feb2020.csv', index=False)